In [15]:
!pip install pandas python-docx
!pip install pywin32 python-docx
!pip install openpyxl

In [2]:
import os
import zipfile
import pandas as pd
from docx import Document

In [5]:
##33.zip others.zip ile ayni

# Define the path where the ZIP files are located
zip_files_path = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'
unzip_folders_path = zip_files_path  # Assuming you want to unzip in the same location

# Unzip each ZIP file into a different subfolder
for filename in os.listdir(zip_files_path):
    if filename.endswith('.zip'):
        # Create a subfolder for the contents of this ZIP file
        subfolder_name = os.path.splitext(filename)[0]
        subfolder_path = os.path.join(unzip_folders_path, subfolder_name)
        os.makedirs(subfolder_path, exist_ok=True)
        
        # Unzip the ZIP file into the subfolder
        zip_file_path = os.path.join(zip_files_path, filename)
        with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
            zip_ref.extractall(subfolder_path)
        print(f"Unzipped {filename} into {subfolder_path}")

      

Unzipped 1.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\1
Unzipped 10.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\10
Unzipped 11.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\11
Unzipped 12.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\12
Unzipped 13.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\13
Unzipped 14.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\14
Unzipped 15.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\15
Unzipped 16.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\16
Unzipped 17.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\17
Unzipped 18.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\18
Unzipped 19.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\19
Unzipped 2.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\2
Unzipped 20.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\20
Unzipped 21.zip into C:\Users\muc574\Bid Protest\WestLaw Data\Data\21
Unzipped 22.zip into C:\

### Step 1 - Read Doc Files into CSV

In [6]:
##export conclusion sections
import csv
import os
import re

def save_final_clean_text_to_csv(root_dir, csv_filename='final_clean_text.csv'):
    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['Subdir', 'Filename', 'Final Clean Text'])

        # Cleanup pattern to remove RTF control words, formatting characters, braces, and reduce all kinds of whitespace
        cleanup_pattern = re.compile(r'(\\par|\\[a-z]+\d*|\{\}|\{|\}|\n|\r|\t|\f|\v|\s{2,})')

        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                if filename.endswith('.doc'):  # Adjust as necessary for your file types
                    file_path = os.path.join(subdir, filename)
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()

                            # Find all occurrences of "conclusion" and "All Citations"
                            conclusions = [(m.start(0), m.end(0)) for m in re.finditer('conclusion', content, re.IGNORECASE | re.DOTALL)]
                            all_citations = [(m.start(0), m.end(0)) for m in re.finditer('All Citations', content, re.IGNORECASE | re.DOTALL)]

                            # Determine the last "conclusion" before the last "All Citations", if "All Citations" exists
                            if all_citations:
                                last_citation_start, _ = all_citations[-1]
                                conclusions_before_last_citation = [end for start, end in conclusions if start < last_citation_start]
                                if conclusions_before_last_citation:
                                    conclusion_end = conclusions_before_last_citation[-1]
                                    all_citations_start = last_citation_start
                                    text_after_conclusion_before_citations = content[conclusion_end:all_citations_start].strip()
                                else:
                                    continue  # Skip if no valid conclusion before last "All Citations"
                            else:
                                # If "All Citations" does not exist, use the last "conclusion"
                                if conclusions:
                                    _, conclusion_end = conclusions[-1]
                                    text_after_conclusion_before_citations = content[conclusion_end:].strip()
                                else:
                                    continue  # Skip if no "conclusion" at all

                            # Further cleanup of the text, including reducing excessive whitespace
                            clean_text = re.sub(cleanup_pattern, ' ', text_after_conclusion_before_citations).strip()
                            # Additional step to ensure the text is a coherent paragraph
                            coherent_paragraph = ' '.join(clean_text.split())
                            print(f"File: {filename}, Final Clean Text: {coherent_paragraph[:100]}...")
                            csvwriter.writerow([subdir, filename, coherent_paragraph])
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_final_clean_text_to_csv(root_directory)

File: 001 - PDS Consultants Inc v United States.doc, Final Clean Text: For all of these reasons, the court GRANTS IFB s motion for a stay pending appeal. The VA may contin...
File: 002 - Veterans Contracting Group Inc v United States.doc, Final Clean Text: For the reasons stated, Veterans motion for a preliminary injunction is GRANTED IN PART and the gove...
File: 003 - Q Integrated Companies LLC v United States.doc, Final Clean Text: For the foregoing reasons, Q Integrated is awarded bid preparation and proposal costs of $21,124.47 ...
File: 004 - In re Global Computer Enterprises Inc.doc, Final Clean Text: For the foregoing reasons, the Court finds in favor of the Defendant on Count III (Legal Malpractice...
File: 005 - AT And T Corp v United States.doc, Final Clean Text: For the foregoing reasons, the Court concludes that the decision to override the CICA stay of perfor...
File: 006 - Automated Collection Services Inc v United States.doc, Final Clean Text: [.] \'3f). With respect to

In [7]:
# Path to the directory
root_dir = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Counter for .doc files
doc_file_count = 0

# Walk through the directory and its subdirectories
for subdir, dirs, files in os.walk(root_dir):
    for file in files:
        if file.endswith('.doc'):
            doc_file_count += 1

# Print the number of .doc files
print(f"Number of .doc files under {root_dir}: {doc_file_count}")


Number of .doc files under C:\Users\muc574\Bid Protest\WestLaw Data\Data: 3405


### Step 2 - Convert to XL

In [8]:
import pandas as pd

# Read the CSV file
df = pd.read_csv('final_clean_text.csv')

# Filter rows where 'Subdir' column contains the specified path
filtered_df = df[df['Subdir'].str.contains(r'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data\\.*', regex=True)]

# Save the filtered data to an XLSX file using openpyxl
filtered_df.to_excel('final_clean_text_2.xlsx', index=False, engine='openpyxl')


In [9]:
filtered_df.head()

Subdir  \
0  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
1  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
2  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
3  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
4  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   

                                            Filename  \
0      001 - PDS Consultants Inc v United States.doc   
1  002 - Veterans Contracting Group Inc v United ...   
2  003 - Q Integrated Companies LLC v United Stat...   
3    004 - In re Global Computer Enterprises Inc.doc   
4            005 - AT And T Corp v United States.doc   

                                    Final Clean Text  
0  For all of these reasons, the court GRANTS IFB...  
1  For the reasons stated, Veterans motion for a ...  
2  For the foregoing reasons, Q Integrated is awa...  
3  For the foregoing reasons, the Court finds in ...  
4  For the foregoing reasons, the Court concludes...

### Step 3 - Now generate data for excluded files

#### Identify excluded files

In [10]:
import os
import pandas as pd

# Path to the directory
root_dir = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Read the Excel file to get the list of subdirectories already included
df = pd.read_excel('final_clean_text_2.xlsx', engine='openpyxl')
included_subdirs = set(df['Filename'])
print(df['Filename'].shape)

# List to store paths of .doc files not included in the Excel file
excluded_files = []
# List to store paths of .doc files not included in the Excel file
excluded_files_long = []


# Walk through the directory and its subdirectories
for subdir, dirs, files in os.walk(root_dir):
    for file in files:
        if file.endswith('.doc'):
            file_path = os.path.join(subdir, file)
            #print(file)
            # Check if the file's directory is not in the list of included subdirectories
            if file not in included_subdirs:
                excluded_files.append(file)
                excluded_files_long.append(file_path)

print(len(excluded_files))

(2817,)
587


#### Extract info from excluded files

In [11]:
import csv
import os
import re

def clean_and_extract_last_100_chars(file_path):
    try:
        with open(file_path, 'r', encoding='utf-8') as file:
            content = file.read()
            # Split and remove all text after "All Citations"
            content = re.split('All Citations', content, flags=re.IGNORECASE)[0]
            # Extended cleanup pattern to also remove specific patterns and sequences of spaces
            cleanup_pattern = re.compile(
                r'(\\par|\\[a-z]+\d*|\{\}|\{|\}|\n|\r|\t|\f|\v|\s{2,}|\\[*]co_allCitations_\d+\\[*]co_allCitations_\d+|\s{5,})'
            )
            clean_content = re.sub(cleanup_pattern, '', content).strip()
            return clean_content[-1000:]
    except Exception as e:
        print(f"Error reading file {file_path}: {e}")
        return None

# Prepare to write to a CSV file
with open('additionaldata.csv', 'w', newline='', encoding='utf-8') as csvfile:
    csvwriter = csv.writer(csvfile)
    csvwriter.writerow(['Subdir', 'Filename', 'Final Clean Text'])

    for file_path in excluded_files_long:
        print(file_path)
        last_100_chars = clean_and_extract_last_100_chars(file_path)
        if last_100_chars:
            directory, filename = os.path.split(file_path)
            csvwriter.writerow([directory, filename, last_100_chars])


C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\007 - Mail Transportation Inc v United States.doc
C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\008 - Mail Transportation Inc v United States.doc
C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\010 - Account Control Technology Inc v United States.doc
C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\011 - Van Ru Credit Corporation v United States.doc
C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\012 - Collection Technology Inc v United States.doc
C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\013 - Continental Services Group Inc v United States.doc
C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\014 - Alltran Educations Inc v United States.doc
C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\028 - National Mall Tours of Washington Inc v United States Department of the In.doc
C:\Users\muc574\Bid Protest\WestLaw Data\Data\1\030 - Board of Regents of Nevada System of Higher Education on behalf of Desert .doc
C:\Users\muc574\Bid Protest\Wes

### Step 4 - Merge all data

In [12]:
import pandas as pd
import os

# Read the CSV file
df_csv = pd.read_csv('additionaldata.csv')

# Read the Excel file
df_excel = pd.read_excel('final_clean_text_2.xlsx', engine='openpyxl')

# Append the dataframes
df_combined = df_csv.append(df_excel, ignore_index=True)

# Export the combined dataframe to a new Excel file
df_combined.to_excel('final_clean_text_3.xlsx', index=False, engine='openpyxl')

# Confirm the number of rows in the final dataframe is equal to the sum of the rows in each
print(f"Rows in additionaldata.csv: {df_csv.shape[0]}")
print(f"Rows in final_clean_text_2.xlsx: {df_excel.shape[0]}")
print(f"Rows in combined dataframe: {df_combined.shape[0]}")
assert df_combined.shape[0] == df_csv.shape[0] + df_excel.shape[0], "Row counts do not match."



C:\Users\muc574\AppData\Local\Temp\ipykernel_26992\1100021393.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_combined = df_csv.append(df_excel, ignore_index=True)


Rows in additionaldata.csv: 587
Rows in final_clean_text_2.xlsx: 2817
Rows in combined dataframe: 3404


### Step 5 - Calculate rejection rates

Case outcomes in legal proceedings can be categorized into several typical categories, depending on the context of the legal system and the nature of the case (civil, criminal, administrative, etc.). Below are some common outcome categories:

Dismissed: The case is thrown out by the judge without a trial or further hearing, often due to lack of evidence, procedural errors, or jurisdictional issues.

Denied: In the context of motions or specific legal requests within a case, the judge decides not to grant the request.

Granted: Opposite of denied, where the judge decides to approve a motion or request made by one of the parties.

Judgment: A final decision by the judge or jury regarding the case. This can result in several specific outcomes, such as:

For the plaintiff (or prosecutor in criminal cases): The case is won by the party bringing the lawsuit (or the state in criminal matters), and damages or specific actions may be awarded.
For the defendant: The case is won by the party defending against the lawsuit or charges, leading to no action required or damages awarded against them.
Settled: The parties come to an agreement before the final judgment, often resulting in a financial settlement or other terms that both parties agree to, which resolves the dispute.

Convicted: In criminal cases, this means the defendant is found guilty of the charges against them.

Acquitted: In criminal cases, the defendant is found not guilty of the charges against them.

Summary Judgment: A legal decision made by the court without a full trial, typically because one party is entitled to judgment as a matter of law, based on the evidence presented.

Appeal: One of the parties requests a higher court to review the decision made by a lower court, which can lead to the decision being upheld, reversed, or remanded for further proceedings.

Remanded: The case is sent back to a lower court from an appellate court for further action or a new trial, often due to procedural errors or issues identified by the appellate court.

These categories represent the general outcomes that can occur in legal proceedings, although specific terms and processes can vary based on jurisdiction and the type of law involved (criminal, civil, family law, etc.).

In [13]:
import pandas as pd
import numpy as np
import re

# Read the Excel file
df = pd.read_excel('final_clean_text_3.xlsx', engine='openpyxl')

# Function to check if the patterns "denied" or "sustained" exist in the text
def contains_pattern(text, pattern):
    if pd.isna(text):
        return 0
    return 1 if re.search(pattern, text, re.IGNORECASE) else 0

# Generate dummy variables
df['contains_denied'] = df['Final Clean Text'].apply(lambda x: contains_pattern(x, 'denied'))
df['contains_rejected'] = df['Final Clean Text'].apply(lambda x: contains_pattern(x, 'rejected'))
df['contains_dismissed'] = df['Final Clean Text'].apply(lambda x: contains_pattern(x, 'dismissed'))
df['contains_remanded'] = df['Final Clean Text'].apply(lambda x: contains_pattern(x, 'remanded'))


df['contains_settled'] = df['Final Clean Text'].apply(lambda x: contains_pattern(x, 'settled'))

# Optional: save the updated dataframe with dummy variables to a new Excel file
df.to_excel('final_clean_text_4.xlsx', index=False, engine='openpyxl')

df.head()


Subdir  \
0  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
1  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
2  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
3  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
4  C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   

                                            Filename  \
0  007 - Mail Transportation Inc v United States.doc   
1  008 - Mail Transportation Inc v United States.doc   
2  010 - Account Control Technology Inc v United ...   
3  011 - Van Ru Credit Corporation v United State...   
4  012 - Collection Technology Inc v United State...   

                                    Final Clean Text  contains_denied  \
0  HYPERLINK "https://www.westlaw.com/Link/Docume...                0   
1   conversion serves the public interest, an inj...                1   
2  a947fe08ef5e04eeedbf79e1eebe33c5c31feedea87c41...                0   
3  5ad879fb8d2e86f4d2245807cb00009aa61f3e7c4892e4...                0   
4  686363039e5feb04f01211168160a6f6e8d123ad561b1c...                0   

   contains_rejected  contains_dismissed  contains_remanded  contains_settled  
0                  0                   0                  0                 0  
1                  0                   0                  0                 0  
2                  0                   0                  0                 0  
3                  0                   0                  0                 0  
4                  0                   0                  0                 0

In [14]:
df.describe()

contains_denied  contains_rejected  contains_dismissed  \
count      3404.000000        3404.000000         3404.000000   
mean          0.454465           0.037015            0.159224   
std           0.497995           0.188827            0.365939   
min           0.000000           0.000000            0.000000   
25%           0.000000           0.000000            0.000000   
50%           0.000000           0.000000            0.000000   
75%           1.000000           0.000000            0.000000   
max           1.000000           1.000000            1.000000   

       contains_remanded  contains_settled  
count        3404.000000       3404.000000  
mean            0.056110          0.017920  
std             0.230169          0.132681  
min             0.000000          0.000000  
25%             0.000000          0.000000  
50%             0.000000          0.000000  
75%             0.000000          0.000000  
max             1.000000          1.000000

### Step 6 - Rule of Two

In [15]:
import csv
import os
import re  # Import the regular expression module

def clean_text(text):
    # Replace the specific sequences with desired characters or an empty string
    text = text.replace('u8220' , "")  # Example: replacing with a standard left double quotation mark
    text = text.replace('u8221' , "")  # Example: replacing with a standard right double quotation mark
    text = text.replace('\\\'3f', '')  # Removes the sequence \'3f correctly

    # Add more replacements as needed
    return text

    
def save_paragraphs_with_regex_to_csv(root_dir, csv_filename='paragraphs_with_regex_rule_of_two.csv'):
    # Compile the regular expression for efficiency in a loop
    pattern = re.compile(r'rule of two', re.IGNORECASE)  # Case-insensitive search

    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['Subdir','Filename', 'Paragraph'])  # Write the header

        # Iterate through all subdirectories of the root directory
        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                if ".doc" in filename:
                    file_path = os.path.join(subdir, filename)
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()  # Read the entire file into a single string
                            paragraphs = content.split('\n')  # Split the content into paragraphs
                            for paragraph in paragraphs:
                                if pattern.search(paragraph):  # Use re.search to find the pattern
                                    paragraph = clean_text(paragraph)
                                    print(f"Dir: {subdir}, File: {filename}, Paragraph with 'The Rule of Two': {paragraph}")  # Keep printing
                                    csvwriter.writerow([subdir,filename, paragraph])  # Save to CSV
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_paragraphs_with_regex_to_csv(root_directory)


Dir: C:\Users\muc574\Bid Protest\WestLaw Data\Data\1, File: 001 - PDS Consultants Inc v United States.doc, Paragraph with 'The Rule of Two': , in SDVOSB\rquote s bid protest challenging Veterans Administration\rquote s (VA) continued procurement of eyewear products and services from AbilityOne procurement list created under Javits-Wagner-O\rquote Day Act (JWOD) before first applying \rule of two\ analysis prescribed under Veterans Benefits, Health Care, and Information Technology Act (VBA), incumbent contractor filed motion, as defendant-intervenor, seeking stay pending appeal.
Dir: C:\Users\muc574\Bid Protest\WestLaw Data\Data\1, File: 001 - PDS Consultants Inc v United States.doc, Paragraph with 'The Rule of Two': The Veterans Benefits, Health Care, and Information Technology Act (VBA) generally requires the Veterans Administration (VA) to set goals for providing contracts to veteran-owned small businesses (VOSBs), with a special preference for service-disabled veteran-owned small bu

In [16]:
import os
import pandas as pd

# Step 1: Loop each '.doc' file under all subdirectories
root_dir = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'
doc_files = []
for subdir, dirs, files in os.walk(root_dir):
    for file in files:
        if file.endswith('.doc'):
            doc_files.append([subdir, file])

# Step 2: Produce a dataframe that includes [subdir (excluding filename), filename]
df_doc_files = pd.DataFrame(doc_files, columns=['Subdir', 'Filename'])
df_doc_files['rule_of_two'] = 0  # By construction, set 'rule_of_two' to zero

# Step 3: Check if [Subdir, Filename] exist in [Subdir, Filename] of 'paragraphs_with_regex_rule_of_two.xlsx'
df_rule_of_two = pd.read_csv('paragraphs_with_regex_rule_of_two.csv')
df_doc_files['rule_of_two'] = df_doc_files.apply(lambda row: 1 if any(
    (df_rule_of_two['Subdir'] == row['Subdir']) & (df_rule_of_two['Filename'] == row['Filename'])) else 0, axis=1)

# Step 4: Count the unique number of [Subdir, Filename] in 'paragraphs_with_regex_rule_of_two.xlsx'
unique_rule_of_two = df_rule_of_two[['Subdir', 'Filename']].drop_duplicates().shape[0]
print(f"Unique [Subdir, Filename] in paragraphs_with_regex_rule_of_two.xlsx: {unique_rule_of_two}")

# Step 5: Count the sum of variable 'rule_of_two'
sum_rule_of_two = df_doc_files['rule_of_two'].sum()
print(f"Sum of 'rule_of_two': {sum_rule_of_two}")


Unique [Subdir, Filename] in paragraphs_with_regex_rule_of_two.xlsx: 31
Sum of 'rule_of_two': 31


In [18]:
df_doc_files.describe()

rule_of_two
count  3405.000000
mean      0.009104
std       0.094995
min       0.000000
25%       0.000000
50%       0.000000
75%       0.000000
max       1.000000

### Step 7 - Small Business

In [19]:
import csv
import os
import re  # Import the regular expression module

def clean_text(text):
    # Replace the specific sequences with desired characters or an empty string
    text = text.replace('u8220' , "")  # Example: replacing with a standard left double quotation mark
    text = text.replace('u8221' , "")  # Example: replacing with a standard right double quotation mark
    text = text.replace('\\\'3f', '')  # Removes the sequence \'3f correctly

    # Add more replacements as needed
    return text

    
def save_paragraphs_with_regex_to_csv(root_dir, csv_filename='paragraphs_with_regex_sb.csv'):
    # Compile the regular expression for efficiency in a loop
    pattern = re.compile(r'small business', re.IGNORECASE)  # Case-insensitive search

    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['Subdir','Filename', 'Paragraph'])  # Write the header

        # Iterate through all subdirectories of the root directory
        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                if ".doc" in filename:
                    file_path = os.path.join(subdir, filename)
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()  # Read the entire file into a single string
                            paragraphs = content.split('\n')  # Split the content into paragraphs
                            for paragraph in paragraphs:
                                if pattern.search(paragraph):  # Use re.search to find the pattern
                                    paragraph = clean_text(paragraph)
                                    print(f"Dir: {subdir}, File: {filename}, Paragraph with 'The Rule of Two': {paragraph}")  # Keep printing
                                    csvwriter.writerow([subdir,filename, paragraph])  # Save to CSV
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_paragraphs_with_regex_to_csv(root_directory)


Dir: C:\Users\muc574\Bid Protest\WestLaw Data\Data\1, File: 001 - PDS Consultants Inc v United States.doc, Paragraph with 'The Rule of Two':  After service-disabled veteran-owned small business (SDVOSB) was granted judgment on administrative record, by the Court of Federal Claims, 
Dir: C:\Users\muc574\Bid Protest\WestLaw Data\Data\1, File: 001 - PDS Consultants Inc v United States.doc, Paragraph with 'The Rule of Two': The Veterans Benefits, Health Care, and Information Technology Act (VBA) generally requires the Veterans Administration (VA) to set goals for providing contracts to veteran-owned small businesses (VOSBs), with a special preference for service-disabled veteran-owned small businesses (SDVOSBs), and further requires that the VA perform a \rule of two\ analysis to determine whether at least two VOSBs are capable of performing the work at fair market value before procuring goods and services; if the rule of two is met, the VA must conduct the competition for such products or

In [20]:
import os
import pandas as pd

# Step 1: Loop each '.doc' file under all subdirectories
root_dir = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'
doc_files = []
for subdir, dirs, files in os.walk(root_dir):
    for file in files:
        if file.endswith('.doc'):
            doc_files.append([subdir, file])

# Step 2: Produce a dataframe that includes [subdir (excluding filename), filename]
df_doc_files = pd.DataFrame(doc_files, columns=['Subdir', 'Filename'])
df_doc_files['small_business'] = 0  # By construction, set 'small_business' to zero

# Step 3: Check if [Subdir, Filename] exist in [Subdir, Filename] of 'paragraphs_with_regex_small_business.xlsx'
df_small_business = pd.read_csv('paragraphs_with_regex_sb.csv')
df_doc_files['small_business'] = df_doc_files.apply(lambda row: 1 if any(
    (df_small_business['Subdir'] == row['Subdir']) & (df_small_business['Filename'] == row['Filename'])) else 0, axis=1)

# Step 4: Count the unique number of [Subdir, Filename] in 'paragraphs_with_regex_small_business.xlsx'
unique_small_business = df_small_business[['Subdir', 'Filename']].drop_duplicates().shape[0]
print(f"Unique [Subdir, Filename] in paragraphs_with_regex_small_business.xlsx: {unique_small_business}")

# Step 5: Count the sum of variable 'small_business'
sum_small_business = df_doc_files['small_business'].sum()
print(f"Sum of 'small_business': {sum_small_business}")


Unique [Subdir, Filename] in paragraphs_with_regex_small_business.xlsx: 974
Sum of 'small_business': 974


In [21]:
df_doc_files

Subdir  \
0     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
1     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
2     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
3     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
4     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
...                                               ...   
3400  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   
3401  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   
3402  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   
3403  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   
3404  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   

                                               Filename  small_business  
0         001 - PDS Consultants Inc v United States.doc               1  
1     002 - Veterans Contracting Group Inc v United ...               1  
2     003 - Q Integrated Companies LLC v United Stat...               1  
3       004 - In re Global Computer Enterprises Inc.doc               0  
4               005 - AT And T Corp v United States.doc               0  
...                                                 ...             ...  
3400               95 - Nilson Van And Storage v US.doc               0  
3401  96 - L-3 Communications Integrated Systems LP ...               0  
3402                97 - Acrow Corp of America v US.doc               0  
3403                 98 - Fulcra Worldwide LLC v US.doc               0  
3404  99 - Washington Consulting Group Inc v Raytheo...               0  

[3405 rows x 3 columns]

In [22]:
df_doc_files.describe()

small_business
count     3405.000000
mean         0.286050
std          0.451979
min          0.000000
25%          0.000000
50%          0.000000
75%          1.000000
max          1.000000

### Step 8 - Veteran Business

In [23]:
import csv
import os
import re  # Import the regular expression module

def clean_text(text):
    # Replace the specific sequences with desired characters or an empty string
    text = text.replace('u8220' , "")  # Example: replacing with a standard left double quotation mark
    text = text.replace('u8221' , "")  # Example: replacing with a standard right double quotation mark
    text = text.replace('\\\'3f', '')  # Removes the sequence \'3f correctly

    # Add more replacements as needed
    return text

    
def save_paragraphs_with_regex_to_csv(root_dir, csv_filename='paragraphs_with_regex_vet.csv'):
    # Compile the regular expression for efficiency in a loop
    pattern = re.compile(r'veteran', re.IGNORECASE)  # Case-insensitive search

    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['Subdir','Filename', 'Paragraph'])  # Write the header

        # Iterate through all subdirectories of the root directory
        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                if ".doc" in filename:
                    file_path = os.path.join(subdir, filename)
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()  # Read the entire file into a single string
                            paragraphs = content.split('\n')  # Split the content into paragraphs
                            for paragraph in paragraphs:
                                if pattern.search(paragraph):  # Use re.search to find the pattern
                                    paragraph = clean_text(paragraph)
                                    print(f"Dir: {subdir}, File: {filename}, Paragraph with 'Veteran: {paragraph}")  # Keep printing
                                    csvwriter.writerow([subdir,filename, paragraph])  # Save to CSV
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_paragraphs_with_regex_to_csv(root_directory)


Dir: C:\Users\muc574\Bid Protest\WestLaw Data\Data\1, File: 001 - PDS Consultants Inc v United States.doc, Paragraph with 'Veteran:  After service-disabled veteran-owned small business (SDVOSB) was granted judgment on administrative record, by the Court of Federal Claims, 
Dir: C:\Users\muc574\Bid Protest\WestLaw Data\Data\1, File: 001 - PDS Consultants Inc v United States.doc, Paragraph with 'Veteran: , in SDVOSB\rquote s bid protest challenging Veterans Administration\rquote s (VA) continued procurement of eyewear products and services from AbilityOne procurement list created under Javits-Wagner-O\rquote Day Act (JWOD) before first applying \rule of two\ analysis prescribed under Veterans Benefits, Health Care, and Information Technology Act (VBA), incumbent contractor filed motion, as defendant-intervenor, seeking stay pending appeal.
Dir: C:\Users\muc574\Bid Protest\WestLaw Data\Data\1, File: 001 - PDS Consultants Inc v United States.doc, Paragraph with 'Veteran: The Javits-Wagner-

In [24]:
import os
import pandas as pd

# Step 1: Loop each '.doc' file under all subdirectories
root_dir = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'
doc_files = []
for subdir, dirs, files in os.walk(root_dir):
    for file in files:
        if file.endswith('.doc'):
            doc_files.append([subdir, file])

# Step 2: Produce a dataframe that includes [subdir (excluding filename), filename]
df_doc_files = pd.DataFrame(doc_files, columns=['Subdir', 'Filename'])
df_doc_files['veteran'] = 0  # By construction, set 'veteran' to zero

# Step 3: Check if [Subdir, Filename] exist in [Subdir, Filename] of 'paragraphs_with_regex_veteran.xlsx'
df_veteran = pd.read_csv('paragraphs_with_regex_vet.csv')
df_doc_files['veteran'] = df_doc_files.apply(lambda row: 1 if any(
    (df_veteran['Subdir'] == row['Subdir']) & (df_veteran['Filename'] == row['Filename'])) else 0, axis=1)

# Step 4: Count the unique number of [Subdir, Filename] in 'paragraphs_with_regex_veteran.xlsx'
unique_veteran = df_veteran[['Subdir', 'Filename']].drop_duplicates().shape[0]
print(f"Unique [Subdir, Filename] in paragraphs_with_regex_veteran.xlsx: {unique_veteran}")

# Step 5: Count the sum of variable 'veteran'
sum_veteran = df_doc_files['veteran'].sum()
print(f"Sum of 'veteran': {sum_veteran}")


Unique [Subdir, Filename] in paragraphs_with_regex_veteran.xlsx: 353
Sum of 'veteran': 353


In [25]:
df_doc_files

Subdir  \
0     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
1     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
2     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
3     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
4     C:\Users\muc574\Bid Protest\WestLaw Data\Data\1   
...                                               ...   
3400  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   
3401  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   
3402  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   
3403  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   
3404  C:\Users\muc574\Bid Protest\WestLaw Data\Data\9   

                                               Filename  veteran  
0         001 - PDS Consultants Inc v United States.doc        1  
1     002 - Veterans Contracting Group Inc v United ...        1  
2     003 - Q Integrated Companies LLC v United Stat...        0  
3       004 - In re Global Computer Enterprises Inc.doc        0  
4               005 - AT And T Corp v United States.doc        0  
...                                                 ...      ...  
3400               95 - Nilson Van And Storage v US.doc        0  
3401  96 - L-3 Communications Integrated Systems LP ...        0  
3402                97 - Acrow Corp of America v US.doc        0  
3403                 98 - Fulcra Worldwide LLC v US.doc        0  
3404  99 - Washington Consulting Group Inc v Raytheo...        0  

[3405 rows x 3 columns]

In [129]:
df_doc_files.describe()

veteran
count  3169.000000
mean      0.106027
std       0.307921
min       0.000000
25%       0.000000
50%       0.000000
75%       0.000000
max       1.000000

In [27]:
import os

def save_paragraphs_with_dollar_sign_to_csv(root_dir, csv_filename='paragraphs_with_dollar.csv'):
    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['subdir', 'Filename', 'Paragraph'])  # Write the header

        # Iterate through all subdirectories of the root directory
        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                file_path = os.path.join(subdir, filename)
                if ".doc" in filename:
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()  # Read the entire file into a single string
                            paragraphs = content.split('\n')  # Split the content into paragraphs
                            for paragraph in paragraphs:
                                if 'contract' in paragraph and '$' in paragraph and 'cost' in paragraph:
                                    print(f"File: {filename}, Paragraph with $: {paragraph}")  # Keep printing as requested
                                    csvwriter.writerow([subdir,filename, paragraph])  # Save to CSV
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_paragraphs_with_dollar_sign_to_csv(root_directory)

File: 003 - Q Integrated Companies LLC v United States.doc, Paragraph with $: . Q Integrated sought $145,464.92 in bid costs in its initial application, specifically seeking to recover $71,384.52 in direct labor costs, $42,354.00 in indirect labor costs, $28,894.99 in consultant costs, and $2,831.41 in other costs related to travel, copying, printing, and shipping with regard to the procurement. Pl.\rquote s Reckoning at 4\u8211\'3f6. In addition to its objections regarding the allocation of these costs across multiple contract areas in the procurement, the government specifically objected to labor costs incurred prior to HUD\rquote s issuance of the solicitation, the per-hour labor rate applied by Q Integrated for its two principals, Michael Ognek and Christopher Ognek, the rate used to calculate indirect labor costs as a percentage of direct labor costs, certain consulting fees, and certain travel and shipping costs. 
File: 003 - Q Integrated Companies LLC v United States.doc, Paragr

In [3]:
"""import os

def print_first_line_of_files(root_dir):
    # Iterate through all subdirectories of the root directory
    for subdir, dirs, files in os.walk(root_dir):
        for filename in files:
            file_path = os.path.join(subdir, filename)
            if ".doc" in file_path:
                
                try:
                    with open(file_path, 'r', encoding='utf-8') as file:
                        first_line = file.readline().strip()  # Read the first line
                        print(subdir, f"File: {filename}, First line: {first_line}")
                except Exception as e:
                    print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
print_first_line_of_files(root_directory)"""


'import os\n\ndef print_first_line_of_files(root_dir):\n    # Iterate through all subdirectories of the root directory\n    for subdir, dirs, files in os.walk(root_dir):\n        for filename in files:\n            file_path = os.path.join(subdir, filename)\n            if ".doc" in file_path:\n                \n                try:\n                    with open(file_path, \'r\', encoding=\'utf-8\') as file:\n                        first_line = file.readline().strip()  # Read the first line\n                        print(subdir, f"File: {filename}, First line: {first_line}")\n                except Exception as e:\n                    print(f"Error reading file {filename}: {e}")\n\n# Define the root directory\nroot_directory = \'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data\'\n\n# Execute the function with the root directory as its argument\nprint_first_line_of_files(root_directory)'

In [6]:
"""import os
def print_paragraphs_with_dollar_sign(root_dir):
    # Iterate through all subdirectories of the root directory
    for subdir, dirs, files in os.walk(root_dir):
        for filename in files:
            file_path = os.path.join(subdir, filename)
            try:
                with open(file_path, 'r', encoding='utf-8') as file:
                    content = file.read()  # Read the entire file into a single string
                    paragraphs = content.split('\n')  # Split the content into paragraphs
                    for paragraph in paragraphs:
                        if '$' in paragraph:
                            print(f"File: {filename}, Paragraph with $: {paragraph}")
            except Exception as e:
                print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
print_paragraphs_with_dollar_sign(root_directory)"""


'import os\ndef print_paragraphs_with_dollar_sign(root_dir):\n    # Iterate through all subdirectories of the root directory\n    for subdir, dirs, files in os.walk(root_dir):\n        for filename in files:\n            file_path = os.path.join(subdir, filename)\n            try:\n                with open(file_path, \'r\', encoding=\'utf-8\') as file:\n                    content = file.read()  # Read the entire file into a single string\n                    paragraphs = content.split(\'\n\')  # Split the content into paragraphs\n                    for paragraph in paragraphs:\n                        if \'$\' in paragraph:\n                            print(f"File: {filename}, Paragraph with $: {paragraph}")\n            except Exception as e:\n                print(f"Error reading file {filename}: {e}")\n\n# Define the root directory\nroot_directory = \'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data\'\n\n# Execute the function with the root directory as its argument\nprint_par

In [85]:
"""import csv
import os
import re

def save_final_clean_text_to_csv(root_dir, csv_filename='final_clean_text.csv'):
    not_found_list = []  # Step 1: Create an empty list

    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['Subdir', 'Filename', 'Final Clean Text'])

        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                if filename.endswith('.doc'):
                    file_path = os.path.join(subdir, filename)
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()

                            conclusion_match = re.search('conclusion', content, re.IGNORECASE | re.DOTALL)
                            start_pos = None

                            if conclusion_match:
                                start_pos = conclusion_match.end()
                            else:
                                alt_endings_match = re.search('conclusion\.|IT IS ORDERED that', content, re.IGNORECASE | re.DOTALL)
                                if alt_endings_match:
                                    start_pos = alt_endings_match.end()

                            if start_pos is not None:
                                text_after_marker = content[start_pos:].strip()
                                all_citations_position = text_after_marker.find('All Citations')

                                if all_citations_position != -1:
                                    text_before_all_citations = content[start_pos:start_pos + all_citations_position].strip()
                                else:
                                    text_before_all_citations = text_after_marker

                                cleanup_pattern = re.compile(r'(\\par|\\[a-z]+\d*|\{\}|\{|\}|\n|\r|\t|\f|\v|\s{2,})')
                                clean_text = re.sub(cleanup_pattern, ' ', text_before_all_citations).strip()

                                if clean_text:
                                    print(f"Exporting: {filename}, Final Clean Text: {clean_text[:100]}...")
                                    csvwriter.writerow([subdir, filename, clean_text])
                                else:
                                    print(f"No valid clean text for export in {filename}.")
                            else:
                                not_found_list.append(file_path)  # Step 2: Append to the list
                                print(f"No 'conclusion', 'conclusion.', or 'IT IS ORDERED that' found in {filename}.")
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

    # Step 3: Loop through the list and print each item
    print("\nFiles where 'conclusion' or alternatives were not found:")
    for item in not_found_list:
        print(item)

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_final_clean_text_to_csv(root_directory)
"""

'import csv\nimport os\nimport re\n\ndef save_final_clean_text_to_csv(root_dir, csv_filename=\'final_clean_text.csv\'):\n    not_found_list = []  # Step 1: Create an empty list\n\n    with open(csv_filename, \'w\', newline=\'\', encoding=\'utf-8\') as csvfile:\n        csvwriter = csv.writer(csvfile)\n        csvwriter.writerow([\'Subdir\', \'Filename\', \'Final Clean Text\'])\n\n        for subdir, dirs, files in os.walk(root_dir):\n            for filename in files:\n                if filename.endswith(\'.doc\'):\n                    file_path = os.path.join(subdir, filename)\n                    try:\n                        with open(file_path, \'r\', encoding=\'utf-8\') as file:\n                            content = file.read()\n\n                            conclusion_match = re.search(\'conclusion\', content, re.IGNORECASE | re.DOTALL)\n                            start_pos = None\n\n                            if conclusion_match:\n                                start_pos = 

In [76]:
"""#work ok but not perfect
import csv
import os
import re

def save_final_clean_text_to_csv(root_dir, csv_filename='final_clean_text.csv'):
    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['Subdir', 'Filename', 'Final Clean Text'])

        # Adjusted regex pattern to capture text after "conclusion" but stop at "All Citations"
        conclusion_to_citations_pattern = re.compile(r'conclusion(.*?)(?=All Citations)', re.IGNORECASE | re.DOTALL)

        # Enhanced cleanup pattern to remove RTF control words, formatting characters, braces, and reduce all kinds of whitespace
        cleanup_pattern = re.compile(r'(\\par|\\[a-z]+\d*|\{\}|\{|\}|\n|\r|\t|\f|\v|\s{2,})')

        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                if filename.endswith('.doc'):  # Adjust as necessary for your file types
                    file_path = os.path.join(subdir, filename)
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()
                            match = conclusion_to_citations_pattern.search(content)
                            if match:
                                text_after_conclusion_before_citations = match.group(1).strip()
                                # Further cleanup of the text, including reducing excessive whitespace
                                clean_text = re.sub(cleanup_pattern, ' ', text_after_conclusion_before_citations).strip()
                                # Additional step to ensure the text is a coherent paragraph
                                coherent_paragraph = ' '.join(clean_text.split())
                                print(f"File: {filename}, Final Clean Text: {coherent_paragraph[:100]}...")
                                csvwriter.writerow([subdir, filename, coherent_paragraph])
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_final_clean_text_to_csv(root_directory)"""

'#work ok but not perfect\nimport csv\nimport os\nimport re\n\ndef save_final_clean_text_to_csv(root_dir, csv_filename=\'final_clean_text.csv\'):\n    with open(csv_filename, \'w\', newline=\'\', encoding=\'utf-8\') as csvfile:\n        csvwriter = csv.writer(csvfile)\n        csvwriter.writerow([\'Subdir\', \'Filename\', \'Final Clean Text\'])\n\n        # Adjusted regex pattern to capture text after "conclusion" but stop at "All Citations"\n        conclusion_to_citations_pattern = re.compile(r\'conclusion(.*?)(?=All Citations)\', re.IGNORECASE | re.DOTALL)\n\n        # Enhanced cleanup pattern to remove RTF control words, formatting characters, braces, and reduce all kinds of whitespace\n        cleanup_pattern = re.compile(r\'(\\par|\\[a-z]+\\d*|\\{\\}|\\{|\\}|\n|\r|\t|\x0c|\x0b|\\s{2,})\')\n\n        for subdir, dirs, files in os.walk(root_dir):\n            for filename in files:\n                if filename.endswith(\'.doc\'):  # Adjust as necessary for your file types\n        

In [77]:
"""import csv
import os

def save_paragraphs_with_dollar_sign_to_csv(root_dir, csv_filename='paragraphs_with_dollar.csv'):
    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['subdir', 'Filename', 'Paragraph'])  # Write the header

        # Iterate through all subdirectories of the root directory
        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                file_path = os.path.join(subdir, filename)
                if ".doc" in filename:
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()  # Read the entire file into a single string
                            paragraphs = content.split('\n')  # Split the content into paragraphs
                            for paragraph in paragraphs:
                                if 'contract' in paragraph and '$' in paragraph:
                                    print(f"File: {filename}, Paragraph with $: {paragraph}")  # Keep printing as requested
                                    csvwriter.writerow([subdir,filename, paragraph])  # Save to CSV
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_paragraphs_with_dollar_sign_to_csv(root_directory)
"""

'import csv\nimport os\n\ndef save_paragraphs_with_dollar_sign_to_csv(root_dir, csv_filename=\'paragraphs_with_dollar.csv\'):\n    with open(csv_filename, \'w\', newline=\'\', encoding=\'utf-8\') as csvfile:\n        csvwriter = csv.writer(csvfile)\n        csvwriter.writerow([\'subdir\', \'Filename\', \'Paragraph\'])  # Write the header\n\n        # Iterate through all subdirectories of the root directory\n        for subdir, dirs, files in os.walk(root_dir):\n            for filename in files:\n                file_path = os.path.join(subdir, filename)\n                if ".doc" in filename:\n                    try:\n                        with open(file_path, \'r\', encoding=\'utf-8\') as file:\n                            content = file.read()  # Read the entire file into a single string\n                            paragraphs = content.split(\'\n\')  # Split the content into paragraphs\n                            for paragraph in paragraphs:\n                                if 

In [8]:
# rule of two

In [84]:
"""import csv
import os
import re  # Import the regular expression module

def clean_text(text):
    # Replace the specific sequences with desired characters or an empty string
    text = text.replace('u8220' , "")  # Example: replacing with a standard left double quotation mark
    text = text.replace('u8221' , "")  # Example: replacing with a standard right double quotation mark
    text = text.replace('\\\'3f', '')  # Removes the sequence \'3f correctly

    # Add more replacements as needed
    return text

    
def save_paragraphs_with_regex_to_csv(root_dir, csv_filename='paragraphs_with_regex.csv'):
    # Compile the regular expression for efficiency in a loop
    pattern = re.compile(r'Rule of Two', re.IGNORECASE)  # Case-insensitive search

    with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['Subdir','Filename', 'Paragraph'])  # Write the header

        # Iterate through all subdirectories of the root directory
        for subdir, dirs, files in os.walk(root_dir):
            for filename in files:
                if ".doc" in filename:
                    file_path = os.path.join(subdir, filename)
                    try:
                        with open(file_path, 'r', encoding='utf-8') as file:
                            content = file.read()  # Read the entire file into a single string
                            paragraphs = content.split('\n')  # Split the content into paragraphs
                            for paragraph in paragraphs:
                                if pattern.search(paragraph):  # Use re.search to find the pattern
                                    paragraph = clean_text(paragraph)
                                    print(f"Dir: {subdir}, File: {filename}, Paragraph with 'The Rule of Two': {paragraph}")  # Keep printing
                                    csvwriter.writerow([subdir,filename, paragraph])  # Save to CSV
                    except Exception as e:
                        print(f"Error reading file {filename}: {e}")

# Define the root directory
root_directory = 'C:\\Users\\muc574\\Bid Protest\\WestLaw Data\\Data'

# Execute the function with the root directory as its argument
save_paragraphs_with_regex_to_csv(root_directory)
"""

'import csv\nimport os\nimport re  # Import the regular expression module\n\ndef clean_text(text):\n    # Replace the specific sequences with desired characters or an empty string\n    text = text.replace(\'u8220\' , "")  # Example: replacing with a standard left double quotation mark\n    text = text.replace(\'u8221\' , "")  # Example: replacing with a standard right double quotation mark\n    text = text.replace(\'\\\'3f\', \'\')  # Removes the sequence \'3f correctly\n\n    # Add more replacements as needed\n    return text\n\n    \ndef save_paragraphs_with_regex_to_csv(root_dir, csv_filename=\'paragraphs_with_regex.csv\'):\n    # Compile the regular expression for efficiency in a loop\n    pattern = re.compile(r\'Rule of Two\', re.IGNORECASE)  # Case-insensitive search\n\n    with open(csv_filename, \'w\', newline=\'\', encoding=\'utf-8\') as csvfile:\n        csvwriter = csv.writer(csvfile)\n        csvwriter.writerow([\'Subdir\',\'Filename\', \'Paragraph\'])  # Write the header\n